In [1]:
from shapely.geometry import Point
import seaborn as sns
import numpy as np
import pandas as pd
import geopandas as gpd
import matplotlib.pyplot as plt
import matplotlib as mpl
import folium
from folium.plugins import MarkerCluster
from folium.plugins import FastMarkerCluster

In [2]:
tests=pd.read_csv('nuclear_weapon_explosions_1945-1998.csv')
tests.head(3)

Unnamed: 0  latitude  longitude  depth  mb name source Country  \
0           1      41.5       88.5    0.0 NaN    -   BOLT   China   
1           2      41.5       88.5    0.0 NaN    -   BOLT   China   
2           3      41.5       88.5    0.0 NaN    -   BOLT   China   

                datetime  max_yield medium confirmation  salvo  
0  10/16/1964 7:00:00 AM       20.0    Air     presumed      0  
1   5/14/1965 2:00:00 AM       20.0    Air     presumed      0  
2    5/9/1966 8:00:00 AM      200.0    Air     presumed      0

In [3]:
world = gpd.read_file('custom.geo.json')

In [4]:
tests=pd.read_csv('nuclear_weapon_explosions_1945-1998.csv')
tests['geometry'] = tests.apply(lambda x: Point((float(x.longitude), 
                                                         float(x.latitude))), 
                                        axis=1)
tests_geo = gpd.GeoDataFrame(tests, 
                           crs = world.crs, 
                           geometry = tests['geometry'])

In [5]:
tests_geo.geometry.centroid
center = tests_geo.geometry.centroid[42]
area_center = [center.y, center.x]
#GeoSeries.to_crs()
tests_map = folium.Map(location =  area_center, zoom_start = 12)

<ipython-input-5-8aa9c7ecd3b7>:1: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  tests_geo.geometry.centroid
<ipython-input-5-8aa9c7ecd3b7>:2: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  center = tests_geo.geometry.centroid[42]


In [6]:
i = 0
for row_index, row_values in tests_geo.iterrows():
    if i <3: 
        print('index is', row_index)
        print('values are:')
        print(' ')
        print(row_values)
        print('------------------------- ')
        i+=1

index is 0
values are:
 
Unnamed: 0                          1
latitude                         41.5
longitude                        88.5
depth                             0.0
mb                                NaN
name                                -
source                           BOLT
Country                         China
datetime        10/16/1964 7:00:00 AM
max_yield                        20.0
medium                            Air
confirmation                 presumed
salvo                               0
geometry            POINT (88.5 41.5)
Name: 0, dtype: object
------------------------- 
index is 1
values are:
 
Unnamed: 0                         2
latitude                        41.5
longitude                       88.5
depth                            0.0
mb                               NaN
name                               -
source                          BOLT
Country                        China
datetime        5/14/1965 2:00:00 AM
max_yield                       20.

In [8]:
#draw our zip code area: 37207
tests_map = folium.Map(location =  area_center, zoom_start = 5)

marker_cluster = MarkerCluster().add_to(tests_map)

folium.GeoJson(tests_geo).add_to(tests_map)

#iterate through stops_in_37207 to create locations and markers 
#for each bus stop
#remember for Folium locations, lat is listed first!!

for row_index, row_values in tests_geo.iterrows():
    loc = [row_values['latitude'], row_values['longitude']]
    pop = str(row_values['max_yield'])
    icon=folium.Icon(color="blue",icon="bus", prefix='fa')
    
    marker = folium.Marker(
        location = loc, 
        popup = pop, icon = icon) 

    marker.add_to(marker_cluster)
#world_plants.save('../maps/map37207.html')

#display our map
tests_map